# Binary Encoding & (1+1) ES

## Core Functions

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
np.random.seed(42)

In [ ]:
# Binary Encoding
def logical2real(logical_vector, a, b):
    """
    Convert a binary-encoded vector to a real value within [a,b]

    Parameters:
    - logical_vector: binary encoded solution (numpy array of 0s and 1s)
    - a: lower bound of search interval
    - b: upper bound of search interval

    Returns:
    - Real-valued number in (a,b) corresponding to the binary encoding

    Mathematical Formulation:
    The conversion follows these steps:
    1. Convert binary string to unsigned integer
    2. Normalize to [0,1) range
    3. Map to (a,b) interval with proper scaling

    Example:
    >>> logical2real(np.array([1, 1, 0]), 13, 17)
    """
    n = len(logical_vector)
    # Convert binary vector to decimal integer
    uint_value = np.sum(2**(n - 1 - np.where(logical_vector)[0]))
    # Normalize to [0,1) range
    real_0_1 = uint_value / (2**n)
    # Map to (a,b) interval with proper scaling and centering
    return a + real_0_1 * (b - a) + 0.5 * (b - a) / (2**n)

In [ ]:
# Population Initialization
def init_population(ngenes, popsize=1):
    """
    Initialize random binary population

    Parameters:
    - ngenes: length of binary chromosome
    - popsize: number of individuals in population

    Returns:
    - Binary matrix of shape (popsize, ngenes) with random 0/1 values

    Implementation Note:
    Uses numpy's random number generator for reproducibility
    """
    return np.random.rand(popsize, ngenes) > 0.5

In [ ]:
# Fitness Evaluation Function
def evaluate_fitness(f, population, a, b):
    """
    Evaluate fitness for each individual in a binary-encoded population

    Parameters:
    - f: objective function to minimize
    - population: matrix where each row is a binary-encoded individual
    - a: lower bound of search space
    - b: upper bound of search space

    Returns:
    - Array of fitness values for each individual

    Technical Note:
    Converts each binary individual to real value before evaluation
    """
    fitness = np.zeros(len(population))
    for i in range(len(population)):
        real_val = logical2real(population[i], a, b)
        fitness[i] = f(real_val)
    return fitness

In [ ]:
# Mutation Operator
def uniform_mutation(logical_x, mutation_prob):
    """
    Uniform mutation operator for binary-encoded individuals

    Parameters:
    - logical_x: binary individual to mutate
    - mutation_prob: probability of flipping each bit

    Returns:
    - Mutated copy of the input individual

    Algorithm:
    Each bit has independent probability mutation_prob of being flipped
    """
    # Create copy to avoid modifying input
    mutated = logical_x.copy()
    # Generate mutation mask
    mutation_mask = np.random.rand(len(logical_x)) < mutation_prob
    # Flip selected bits
    mutated[mutation_mask] = ~mutated[mutation_mask]
    return mutated

## (1+1) Evolution Strategy

In [ ]:
def es_1plus1_visual(f, a, b, n_iter, n_genes, mutation_prob):
    """(1+1) ES with enhanced visualization"""
    # Setup figure
    fig = plt.figure(figsize=(15, 6))
    ax1 = fig.add_subplot(1, 2, 1)
    ax2 = fig.add_subplot(1, 2, 2)

    # Plot function
    domain = np.linspace(a, b, 1000)
    ax1.plot(domain, f(domain), 'b-', lw=2, alpha=0.7)
    ax2.plot(domain, f(domain), 'b-', lw=2, alpha=0.7)

    # Initialize
    current_x = init_population(n_genes, 1)[0]
    current_real = logical2real(current_x, a, b)
    current_fitness = f(current_real)

    # Create plot elements
    parent_line, = ax1.plot([], [], 'ko', ms=8, label='Parent')
    child_line, = ax1.plot([], [], 'ro', ms=6, alpha=0.5, label='Child')
    ax1.legend()

    best_line, = ax2.plot([], [], 'go', ms=10, label='Best')
    path_line, = ax2.plot([], [], 'y-', lw=1, alpha=0.5, label='Path')
    ax2.legend()

    # Store optimization history
    history = {'x': [], 'f': [], 'best_x': [], 'best_f': []}

    def update(i):
        """Update function for animation"""
        nonlocal current_x, current_real, current_fitness

        # Generate and evaluate new candidate
        new_x = uniform_mutation(current_x, mutation_prob)
        new_real = logical2real(new_x, a, b)
        new_fitness = f(new_real)

        # Selection
        if new_fitness < current_fitness:
            current_x, current_real, current_fitness = new_x, new_real, new_fitness

        # Update history
        history['x'].append(new_real)
        history['f'].append(new_fitness)
        if not history['best_x'] or new_fitness < history['best_f'][-1]:
            history['best_x'].append(new_real)
            history['best_f'].append(new_fitness)
        else:
            history['best_x'].append(history['best_x'][-1])
            history['best_f'].append(history['best_f'][-1])

        # Update plots
        parent_line.set_data([current_real], [current_fitness])
        child_line.set_data([new_real], [new_fitness])
        best_line.set_data([history['best_x'][-1]], [history['best_f'][-1]])
        path_line.set_data(history['x'], history['f'])
def es_1plus1_visual(f, a, b, n_iter, n_genes, mutation_prob):
    """(1+1) ES with enhanced visualization"""
    # Setup figure
    fig = plt.figure(figsize=(15, 6))
    ax1 = fig.add_subplot(1, 2, 1)
    ax2 = fig.add_subplot(1, 2, 2)

    # Plot function
    domain = np.linspace(a, b, 1000)
    ax1.plot(domain, f(domain), 'b-', lw=2, alpha=0.7)
    ax2.plot(domain, f(domain), 'b-', lw=2, alpha=0.7)

    # Initialize
    current_x = init_population(n_genes, 1)[0]
    current_real = logical2real(current_x, a, b)
    current_fitness = f(current_real)

    # Create plot elements
    parent_line, = ax1.plot([], [], 'ko', ms=8, label='Parent')
    child_line, = ax1.plot([], [], 'ro', ms=6, alpha=0.5, label='Child')
    ax1.legend()

    best_line, = ax2.plot([], [], 'go', ms=10, label='Best')
    path_line, = ax2.plot([], [], 'y-', lw=1, alpha=0.5, label='Path')
    ax2.legend()

    # Store optimization history
    history = {'x': [], 'f': [], 'best_x': [], 'best_f': []}

    def update(i):
        """Update function for animation"""
        nonlocal current_x, current_real, current_fitness

        # Generate and evaluate new candidate
        new_x = uniform_mutation(current_x, mutation_prob)
        new_real = logical2real(new_x, a, b)
        new_fitness = f(new_real)

        # Selection
        if new_fitness < current_fitness:
            current_x, current_real, current_fitness = new_x, new_real, new_fitness

        # Update history
        history['x'].append(new_real)
        history['f'].append(new_fitness)
        if not history['best_x'] or new_fitness < history['best_f'][-1]:
            history['best_x'].append(new_real)
            history['best_f'].append(new_fitness)
        else:
            history['best_x'].append(history['best_x'][-1])
            history['best_f'].append(history['best_f'][-1])

        # Update plots
        parent_line.set_data([current_real], [current_fitness])
        child_line.set_data([new_real], [new_fitness])
        best_line.set_data([history['best_x'][-1]], [history['best_f'][-1]])
        path_line.set_data(history['x'], history['f'])

        ax1.set_title(f'Generation {i+1}\nCurrent Fitness: {current_fitness:.4f}')
        ax2.set_title(f'Best Fitness: {history["best_f"][-1]:.4f}')

        return parent_line, child_line, best_line, path_line

    # Create animation
    ani = FuncAnimation(fig, update, frames=n_iter, interval=200, blit=True)
    plt.close()
    return HTML(ani.to_jshtml())

    # Create animation
    ani = FuncAnimation(fig, update, frames=n_iter, interval=200, blit=True)
    plt.close()
    return HTML(ani.to_jshtml())


In [ ]:
# Run with visualization
def rastrigin(x):
    return 10 + x**2 - 10*np.cos(2*np.pi*x)

es_1plus1_visual(rastrigin, a=-5, b=5, n_iter=50, n_genes=10, mutation_prob=0.2)